In [1]:
import matplotlib.pyplot as plt
import numpy as np
from get_point_history import pget
from point_history import getmes
from get_point_map import get
import datetime
import itertools

In [2]:
from IPython.display import HTML, display

In [3]:
import pandas as pd
import pickle
import folium
from folium import plugins

In [4]:
import plotly.offline as py
import plotly.graph_objs as go
py.init_notebook_mode()

In [5]:
%matplotlib notebook

In [6]:
path='/mnt/web/brey/MATTHEW/HRun/'

In [7]:
#path='/mnt/rmdisk/MATTHEW/'

In [8]:
hurname='MATTHEW'

In [21]:
basename='hur'

In [22]:
date=datetime.date.today()

In [23]:
date_stamp = datetime.datetime.strftime(date,'%d %b %Y %H:%M')

In [24]:
t1='20160929.00'

In [46]:
t2='20161009.12'

In [47]:
sdate=datetime.datetime.strptime(t1,'%Y%m%d.%H')

In [48]:
edate=datetime.datetime.strptime(t2,'%Y%m%d.%H')

In [49]:
fdate=datetime.datetime.strftime(sdate,"%Y%m%d.%H")

In [50]:
ldate=datetime.datetime.strftime(edate,"%Y%m%d.%H")

In [51]:
#ppath=path+'{}/{}/{}/{:02d}/'.format(sdate.year,sdate.month,sdate.day,sdate.hour)

In [52]:
ppath=path+'{}/'.format(t1)

In [53]:
with open(ppath+basename+'.pkl', 'r') as f:
    ptr=pickle.load(f)

In [54]:
ids=ptr.keys()[:10]

In [55]:
ids=[1400, 872, 878, 821]

In [56]:
# to be used for changing the maping point below
near=[]
for i in range(1,5):
    for r in itertools.permutations((-i,0,i),2): near.append(r)


In [67]:
#get data
tota=[]
gnames=[]
gid=[]
blons=[]
blats=[]

for n in ids[:4]:
    #print n
    t,s,plat,plon,bname,bid = getmes(sdate,edate,n)
    dic0={'t_gauge':t, 'sh':[a for [a,b,c] in s], 'tide':[b for [a,b,c] in s], 'ss':[c for [a,b,c] in s]}
    data0=pd.DataFrame(dic0)
    data0=data0.set_index('t_gauge')
    gnames.append(bname)
    gid.append(bid)
    blons.append(plon)
    blats.append(plat)

    try:
        hcw,hw,yz,xz=pget(fdate,ldate,path,basename,ptr[n])
        print yz,xz
        #hcw,hw=get(fdate,fdate,path,basename,plat,plon)
    except Exception as e:
        print e
#        hw=np.empty(np.size(t))
#        hw.fill(np.nan)
#        hcw=t
        try:
            hcw,hw,mlat,mlon,jc,ic=get(t1,t2,path,basename,plat,plon) # map interpolated data
            print hw.sum()
            if hw.sum() == 0.:
                print 'no num data, changing collection point'
                for r in near:
                        plati=float(plat)+.1*r[0]
                        ploni=float(plon)+.1*r[1]
                        print plati,ploni
                        hcw,hw,mlat,mlon,jc,ic=get(t1,t2,path,basename,plati,ploni) # map interpolated data
                        if hw.sum() != 0: break
        except Exception as e:
            print e
    
    #hcw,hw,mlat,mlon,jc,ic=get(t1,t2,path,basename,plat,plon)
        
    dic2={'t_his':hcw, 's_his':hw, 's_map':hw}
    data2=pd.DataFrame.from_dict(dic2)
    data2=data2.set_index('t_his')
    data0=data0.join(data2, how='outer')
    tota.append(data0)

26.4243 -79.0016
872
0.0
no num data, changing collection point
30.572 -81.465
30.572 -81.365
32.028 -80.8824
34.6898 -76.6607


In [58]:
tota=pd.concat(tota, keys=ids)

In [59]:
tota[['sh','tide','ss','s_his','s_map']] = tota[['sh','tide','ss','s_his','s_map']].apply(pd.to_numeric)

In [60]:
tota.head()

sh     ss   tide     s_his     s_map
1400 2016-09-29 00:00:00    NaN    NaN    NaN -0.002921 -0.002921
     2016-09-29 00:01:00  1.611 -0.156  1.767 -0.003633 -0.003633
     2016-09-29 00:02:00    NaN    NaN    NaN -0.003663 -0.003663
     2016-09-29 00:03:00    NaN    NaN    NaN -0.003238 -0.003238
     2016-09-29 00:04:00    NaN    NaN    NaN -0.003567 -0.003567

Create a dataframe with location info

In [61]:
dic3={'ID':gid,'Location':gnames,'lon':blons,'lat':blats}

In [62]:
infor=pd.DataFrame.from_dict(dic3)

In [63]:
infor[['ID','lon','lat']]=infor[['ID','lon','lat']].apply(pd.to_numeric)

In [64]:
infor=infor.set_index(['ID'])

In [65]:
infor.head()

Location     lat     lon
ID                                            
1400   Bahamas - Settlement pt  26.683 -78.983
872   USA - Fernadina_Beach_FL  30.672 -81.465
878      USA - Fort_Pulaski_GA  32.033 -80.902
821          USA - Beaufort_NC  34.720 -76.670

In [66]:
g_url=[]
for i,val in enumerate(ids):
  try:
    idat=tota.xs(val)
    smask=np.isfinite(idat['ss'])
    shmask=np.isfinite(idat)['s_his']
    try:
        trace1 = go.Scatter(x=idat[smask].index.to_pydatetime(),
                            y=idat[smask]['ss'].values,
                            name='Storm Surge Measured')
    except Exception as e:
        print e
        pass    
    try:
        trace2 = go.Scatter(x=idat[shmask].index.to_pydatetime(),
                            y=idat[shmask]['s_his'].values,
                            name='Storm Surge Computed')
    except Exception as e:
        print e
        pass
    
    try:
        trace3 = go.Scatter(x=idat[smask].index.to_pydatetime(),
                            y=idat[smask]['sh'].values,
                            name='Total measured')
    except Exception as e:
        print e
        pass   
    
    try:
        trace4 = go.Scatter(x=idat[smask].index.to_pydatetime(),
                            y=idat[smask]['tide'].values,
                            name='Tide measured')
    except Exception as e:
        print e
        pass    

    try:
        trace5 = go.Scatter(x=idat[smask].index.to_pydatetime(),
                            y=idat[smask]['s_map'].values,
                            name='Storm Surge [map] Computed')
    except Exception as e:
        print e
        pass    

    
    data = [trace1, trace2, trace5]#, trace3, trace4]
    
    layout = dict (title = infor.xs(val)['Location'],
                   yaxis = dict (title = 'Height'))
    fig = dict (data = data, layout = layout )
    py.iplot(fig, show_link = False, image='png')
    
    g = py.plot(fig, show_link = False, filename='tmp/{}/f{}.html'.format(hurname,i), auto_open=False)
    g_url.append(g)
  except:
    pass

In [53]:
g_url

['file:///home/critechuser/REPOS/StormS/report/tmp/MATTHEW/f0.html']

#### save html links

In [135]:
u=[gi.split('/')[-2:] for gi in g_url]

In [136]:
uu=['tmp/'+'/'.join(ui) for ui in u]

In [137]:
uu=[ui[1] for ui in u]

In [138]:
uu

['f0.html', 'f1.html', 'f2.html', 'f3.html']

## make html

In [139]:
html_string = '''
<html>
    <head>
        <link rel="stylesheet" href="https://maxcdn.bootstrapcdn.com/bootstrap/3.3.1/css/bootstrap.min.css">
        <style>body{ margin:0 100; background:whitesmoke; }</style>
    </head>
    <body>
        <h1>TROPICAL STORM '''+hurname+'''</h1>
        '''+date_stamp+'''
        <p></p>
        
        <!-- *** Section 1 *** --->
        <video width=80% height="550" controls>
          <source src="movie.mp4" type="video/mp4" />
          Your browser doe not support the video tag
        </video>
        
        <p></p>
        <!-- *** Section 4 *** --->
          <iframe width=48% height="550" frameborder="0" seamless="seamless" scrolling="no" \
         src="'''+uu[0]+'''?align="left"></iframe>
         <iframe width=48% height="550" frameborder="0" seamless="seamless" scrolling="no" \
         src="'''+uu[1]+'''?align="right"></iframe>

         <iframe width=48% height="550" frameborder="0" seamless="seamless" scrolling="no" \
         src="'''+uu[2]+'''?align="left"></iframe>
         <iframe width=48% height="550" frameborder="0" seamless="seamless" scrolling="no" \
         src="'''+uu[3]+'''?align="right"></iframe>

       <!-- *** Section Ref *** --->
         <h2>REFERENCES</h2>
         
Measured data from National Centres, Estimation from Joint Research Centre (JRC) based on Meteorological Forecasts from European Centre for Medium Weather Forecast (ECMWF) and using the DELTARES-DELFT3D Flow code.
<p></p>
European Centre for Medium Weather Forecast (ECMWF) data: http://www.ecmwf.int/
<p></p>
DELTARES: https://www.deltares.nl/en/
<p></p>
DELFT3D: https://oss.deltares.nl/web/delft3d
<p></p>
    </body>
</html>'''

In [140]:
f = open('tmp/{}/report.html'.format(hurname),'w')
f.write(html_string)
f.close()
